In [3]:
text = ""
with open(
    "./raw_data/dale_carnegie/how_to_win_friends_and_influence_people.txt", "r"
) as f:
    text = f.read()

In [4]:
from langchain_text_splitters import RecursiveCharacterTextSplitter, Language

text_splitter = RecursiveCharacterTextSplitter(
    separators=RecursiveCharacterTextSplitter.get_separators_for_language(
        Language.MARKDOWN
    ),
    chunk_size=4096,
    keep_separator=True,
)

splitted_text = text_splitter.split_text(text)
len(splitted_text)

139

In [10]:
# Semantic Splitting
from langchain.storage import LocalFileStore
from langchain.embeddings.cache import CacheBackedEmbeddings
from langchain_experimental.text_splitter import SemanticChunker
from langchain_openai.embeddings import OpenAIEmbeddings

underlying_embedder = OpenAIEmbeddings(model="text-embedding-3-small")

store = LocalFileStore("./.cache/embeddings")

embedder = CacheBackedEmbeddings.from_bytes_store(
    underlying_embedder, store, namespace=underlying_embedder.model
)

text_splitter = SemanticChunker(embedder)
splitted_text = text_splitter.split_text(text)
len(splitted_text)

207

In [13]:
import pandas as pd

df = pd.DataFrame(splitted_text, columns=["text"])
df.to_parquet(
    "./raw_data/dale_carnegie/how_to_win_friends_and_influence_people.parquet"
)

In [14]:
import pandas as pd

texts = pd.read_parquet(
    "./raw_data/dale_carnegie/how_to_win_friends_and_influence_people.parquet"
)
texts

text
0    # PART ONE: Fundamental Techniques in Handling...
1    So they rationalize, they explain. They can te...
2    F. Skinner, the world-famous psychologist, pro...
3    Johnston of Enid, Oklahoma, is the safety coor...
4    Fall was condemned viciously - condemned as fe...
..                                                 ...
202  Reminders, admonitions, confrontations, with h...
203  Perhaps. But that is what they said to Napoleo...
204  Ernest Gent of Scarsdale, New York, was troubl...
205  She tried coaxing. Neither worked. Then she tr...
206  . PRINCIPLE 9 Make the other person happy abou...

[207 rows x 1 columns]

In [15]:
## texts에서 문장 길이가 짧은 것은 drop 하자
texts["len"] = texts["text"].apply(len)
texts = texts[texts["len"] > 15]
texts = texts.drop("len", axis=1)
texts

text
0    # PART ONE: Fundamental Techniques in Handling...
1    So they rationalize, they explain. They can te...
2    F. Skinner, the world-famous psychologist, pro...
3    Johnston of Enid, Oklahoma, is the safety coor...
4    Fall was condemned viciously - condemned as fe...
..                                                 ...
202  Reminders, admonitions, confrontations, with h...
203  Perhaps. But that is what they said to Napoleo...
204  Ernest Gent of Scarsdale, New York, was troubl...
205  She tried coaxing. Neither worked. Then she tr...
206  . PRINCIPLE 9 Make the other person happy abou...

[180 rows x 1 columns]

In [18]:
# 문장 앞에 .이 오면 제거
texts["text"] = texts["text"].apply(lambda x: x[1:] if x[0] == "." else x)
texts

# 문장에서 좌우 공백 제거
texts["text"] = texts["text"].apply(lambda x: x.strip())
texts

text
0    # PART ONE: Fundamental Techniques in Handling...
1    So they rationalize, they explain. They can te...
2    F. Skinner, the world-famous psychologist, pro...
3    Johnston of Enid, Oklahoma, is the safety coor...
4    Fall was condemned viciously - condemned as fe...
..                                                 ...
202  Reminders, admonitions, confrontations, with h...
203  Perhaps. But that is what they said to Napoleo...
204  Ernest Gent of Scarsdale, New York, was troubl...
205  She tried coaxing. Neither worked. Then she tr...
206  PRINCIPLE 9 Make the other person happy about ...

[180 rows x 1 columns]

In [19]:
texts.to_parquet(
    "./raw_data/dale_carnegie/how_to_win_friends_and_influence_people.parquet"
)

In [20]:
# Dataframe to list
texts = texts["text"].tolist()
texts

['# PART ONE: Fundamental Techniques in Handling People. ## IF YOU WANT TO GATHER HONEY, DON’T KICK OVER THE BEEHIVE\nOn May 7, 1931, the most sensational manhunt New York City had ever known had come to its climax. After weeks of search, “Two Gun” Crowley - the killer, the gunman who didn’t smoke or drink - was at bay, trapped in his sweetheart’s apartment on West End Avenue. One hundred and fifty policemen and detectives laid siege to his top-floor hideway. They chopped holes in the roof; they tried to smoke out Crowley, the “cop killer,” with teargas. Then they mounted their machine guns on surrounding buildings, and for more than an hour one of New York’s fine residential areas reverberated with the crack of pistol fire and the rut-tat-tat of machine guns. Crowley, crouching behind an over- stuffed chair, fired incessantly at the police. Ten thousand excited people watched the battle. Nothing like it ever been seen before on the sidewalks of New York. When Crowley was captured, Pol

In [9]:
from langchain.storage import LocalFileStore
from langchain.embeddings.cache import CacheBackedEmbeddings
from langchain_community.embeddings import HuggingFaceBgeEmbeddings

model_name = "BAAI/bge-large-en"  # BAAI/bge-m3
model_kwargs = {"device": "mps"}
encode_kwargs = {"normalize_embeddings": True}
underlying_embedder = HuggingFaceBgeEmbeddings(
    model_name=model_name,
    model_kwargs=model_kwargs,
    encode_kwargs=encode_kwargs,
)

store = LocalFileStore("./.cache/embeddings")

embedder = CacheBackedEmbeddings.from_bytes_store(
    underlying_embedder, store, namespace=underlying_embedder.model_name
)

In [10]:
from langchain_community.vectorstores import FAISS

vector_store = FAISS.from_texts(texts, embedder)

In [40]:
from langchain_core.runnables import ConfigurableField

retriever = vector_store.as_retriever(search_kwargs={"k": 3}).configurable_fields(
    search_kwargs=ConfigurableField(
        id="search_kwargs",
        name="search_kwargs",
        description="search_kwargs",
    )
)
retriever.with_config(configurable={"search_kwargs": {"k": 1}}).invoke("friend")

[Document(page_content='T. Dutschmann, a telephone engineer, a student of this course, couldn’t get his three-year old daughter to eat breakfast food. The usual scolding, pleading, coaxing methods had all ended in futility. So the parents asked themselves: “How can we make her want to do it?” The little girl loved to imitate her mother, to feel big and grown up; so one morning they put her on a chair and let her make the breakfast food. At just the psychological moment, Father drifted into the kitchen while she was stirring the cereal and she said: “Oh, look, Daddy, I am making the cereal this morning.” She ate two helpings of the cereal without any coaxing, because she was interested in it. She had achieved a feeling of importance; she had found in making the cereal an avenue of self-expression. William Winter once remarked that "self-expression is the dominant necessity of human nature.” Why can’t we adapt this same psychology to business dealings? When we have a brilliant idea, inst

In [178]:
# llm = RunnableLambda(get_chat_completions)
# llm.invoke(prompt.format(USER_QUESTION="좋은 첫인상을 남기려면 어떻게 해야 하나요?"))

AIMessage(content='[\n    "Become genuinely interested in other people.",\n    "Smile.",\n    "Remember that a person\'s name is to that person the sweetest and most important sound in any language."\n]')

In [16]:
from agents.dale_agent import DaleAgent

sentences = DaleAgent().get_sentence_completions(
    "How can I make a good first impression?"
)

In [42]:
docs = [retriever.invoke(sentence) for sentence in sentences]
docs

# flatten list of lists
docs = [item for sublist in docs for item in sublist]
docs

[Document(page_content='You may meet him tomorrow coming down the street. When you get within ten feet of him, he will begin to wag his tail. If you stop and pat him, he will almost jump out of his skin to show you how much he likes you. And you know that behind this show of affection on his part, there are no ulterior motives: he doesn’t want to sell you any real estate, and he doesn’t want to marry you. Did you ever stop to think that a dog is the only animal that doesn’t have to work for a living? A hen has to lay eggs, a cow has to give milk, and a canary has to sing. But a dog makes his living by giving you nothing but love. When I was five years old, my father bought a little yellow-haired pup for fifty cents. He was the light and joy of my childhood. Every afternoon about four-thirty, he would sit in the front yard with his beautiful eyes staring steadfastly at the path, and as soon as he heard my voice or saw me swinging my dinner pail through the buck brush, he was off like a 

In [43]:
sentences = DaleAgent().get_sentence_completions(
    "취업이 잘 안됩니다. 어떻게 해야할까요?"
)
docs = [retriever.invoke(sentence) for sentence in sentences]
docs = [item for sublist in docs for item in sublist]
docs

[Document(page_content='You may meet him tomorrow coming down the street. When you get within ten feet of him, he will begin to wag his tail. If you stop and pat him, he will almost jump out of his skin to show you how much he likes you. And you know that behind this show of affection on his part, there are no ulterior motives: he doesn’t want to sell you any real estate, and he doesn’t want to marry you. Did you ever stop to think that a dog is the only animal that doesn’t have to work for a living? A hen has to lay eggs, a cow has to give milk, and a canary has to sing. But a dog makes his living by giving you nothing but love. When I was five years old, my father bought a little yellow-haired pup for fifty cents. He was the light and joy of my childhood. Every afternoon about four-thirty, he would sit in the front yard with his beautiful eyes staring steadfastly at the path, and as soon as he heard my voice or saw me swinging my dinner pail through the buck brush, he was off like a 

In [44]:
def get_chat_completions(prompt):
    sentences = DaleAgent().get_sentence_completions(prompt)
    docs = [retriever.invoke(sentence) for sentence in sentences]
    return [item for sublist in docs for item in sublist]

In [45]:
get_chat_completions("오늘 면접에서 떨리는데 어떻게 해야할까요?")

[Document(page_content='You may meet him tomorrow coming down the street. When you get within ten feet of him, he will begin to wag his tail. If you stop and pat him, he will almost jump out of his skin to show you how much he likes you. And you know that behind this show of affection on his part, there are no ulterior motives: he doesn’t want to sell you any real estate, and he doesn’t want to marry you. Did you ever stop to think that a dog is the only animal that doesn’t have to work for a living? A hen has to lay eggs, a cow has to give milk, and a canary has to sing. But a dog makes his living by giving you nothing but love. When I was five years old, my father bought a little yellow-haired pup for fifty cents. He was the light and joy of my childhood. Every afternoon about four-thirty, he would sit in the front yard with his beautiful eyes staring steadfastly at the path, and as soon as he heard my voice or saw me swinging my dinner pail through the buck brush, he was off like a 